In [1]:
import numpy as np 
import matplotlib.pyplot as plt
import pandas as pd
import cartopy
from matplotlib.collections import LineCollection
from matplotlib.colors import ListedColormap
#import geopandas as gpd
%matplotlib qt

In [2]:
def load_raw_line_data_csv():
    data = pd.read_csv("obis_seamap_dataset_994_lines.csv", encoding = 'unicode_escape', engine ='python')
    data['datetime_begin'] = pd.to_datetime(data['datetime_begin'])
    data['datetime_end'] = pd.to_datetime(data['datetime_end'])
    return data.sort_values(by='longitude_begin')

In [3]:
lines_raw_data_df = load_raw_line_data_csv()

def get_original_turtle_paths(data):
    begin_points = np.vstack([data['longitude_begin'].to_numpy(), data['latitude_begin'].to_numpy()])
    begin_points = begin_points.T
    end_points = np.vstack([data['longitude_end'].to_numpy(), data['latitude_end'].to_numpy()])
    end_points = end_points.T
    
    def outlier_mask(paths, med_sigma = 15):
        magnitudes = np.abs(paths - np.median(paths))
        mdev = np.median(magnitudes)
        normalized = magnitudes/mdev if mdev else 0
        return normalized < med_sigma
    
    long_mask = outlier_mask(end_points[:, 0] - begin_points[:, 0])
    lat_mask = outlier_mask(end_points[:, 1] - begin_points[:, 1])
    
    full_mask = long_mask * lat_mask
    
    segments = np.concatenate([begin_points, end_points], axis=1)
    segments = segments.reshape((segments.shape[0], 2, 2))
    segments = segments[full_mask]
    
    
    return segments

In [4]:
def show_original_turtle_animation(raw_data_df):
    
    segments = get_original_turtle_paths(raw_data_df)
    
    fig = plt.figure(figsize=(15, 10))
    plt.gca().axis([-40, -10, -15, 0])
    
    atlantic_ocean_bg_img = plt.imread('atlantic_ocean_bg.png')
    plt.imshow(atlantic_ocean_bg_img, extent=[-40, -10, -15, 0])
    for i in range(0, 160):
        lc = LineCollection(segments[:i*10], colors='r')
        plt.gca().add_collection(lc)
        
        plt.draw()
        plt.show()
        plt.pause(0.05)

In [5]:
#show_original_turtle_animation(lines_raw_data_df)

In [6]:
"""
Idea: turtles see each other occasionally. Use the original turtles ahead of simturtle as sampled ground truth trajectories 
to occasionally work off of. Sample when close to some edge. Can use either other turtle's position as goal 
or other turtle's direction as goal. 

The state of a SimTurtle is just:
[long, lat]

"""

timesteps = 130

n_turtles = 25
probability_follow = 1
sightline_long, sightline_lat = 1.2, 1.2 

mu_speed_long = -np.mean(lines_raw_data_df['longitude_end'] - lines_raw_data_df['longitude_begin'])
stddev_speed_long = np.std(lines_raw_data_df['longitude_end'] - lines_raw_data_df['longitude_begin'])
mu_speed_lat = -np.mean(lines_raw_data_df['latitude_end'] - lines_raw_data_df['latitude_begin'])
stddev_speed_lat = np.std(lines_raw_data_df['latitude_end'] - lines_raw_data_df['latitude_begin'])

In [7]:

def generate_simturtle_initial_positions(n_turtles):
    
    # return type is like a LineCollection 
    retval = np.zeros((n_turtles, 2, 2))
    # half along the cape
    retval[:n_turtles//2, 0, 0] = -34.5 
    retval[:n_turtles//2, 0, 1] = np.random.uniform(size=n_turtles//2, low=-10, high=-6)
    
    retval[:n_turtles//2, 1, 0] = retval[:n_turtles//2, 0, 0]
    retval[:n_turtles//2, 1, 1] = retval[:n_turtles//2, 0, 1]
    
    
    # half along the long southern coastline
    retval[n_turtles//2:, 0, 0] = np.random.uniform(size=n_turtles-n_turtles//2, low=-38, high=-34.5)
    retval[n_turtles//2:, 0, 1] = -12 + (37 + retval[n_turtles//2:, 0, 0]) *0.9
    
    retval[n_turtles//2:, 1, 0] = retval[n_turtles//2:, 0, 0]
    retval[n_turtles//2:, 1, 1] = retval[n_turtles//2:, 0, 1]
    return retval

In [8]:
def step_simturtles(turtle_trajectories, n_turtles, ref_trajectories):
    new_edges = np.zeros((n_turtles, 2, 2))
    new_edges[:, 0, :] = turtle_trajectories[len(turtle_trajectories) - n_turtles:, 1, :]
    new_edges[:, 1, :] = turtle_trajectories[len(turtle_trajectories) - n_turtles:, 1, :]
    
    long_gaussian_step = np.random.normal(loc=mu_speed_long, scale=stddev_speed_long, size=(n_turtles))
    lat_gaussian_step = np.random.normal(loc=mu_speed_lat, scale=stddev_speed_lat, size=(n_turtles))
    
    long_follow_step = np.zeros(n_turtles)
    lat_follow_step = np.zeros(n_turtles)
    for j in range(n_turtles):
        sim_long = new_edges[len(new_edges) - n_turtles + j, 0, 0] 
        sim_lat = new_edges[len(new_edges) - n_turtles + j, 0, 1] 
        for k in range(turtle_trajectories.shape[0] // n_turtles, ref_trajectories.shape[0]):
            ref_long = ref_trajectories[k][0][0]
            ref_lat = ref_trajectories[k][0][1]
            if np.abs(ref_long - sim_long) < sightline_long and np.abs(ref_lat - sim_lat) < sightline_lat:
                long_follow_step[j] -= ref_trajectories[k][1][0] - ref_trajectories[k][0][0]
                lat_follow_step[j] = ref_trajectories[k][1][1] - ref_trajectories[k][0][1]
                break 
            elif np.abs(ref_long - sim_long) > 3 * sightline_long and np.abs(ref_lat - sim_lat) > 3 * sightline_lat:
                break 
    follow_mask = np.random.random(n_turtles) < probability_follow
    follow_mask *= np.logical_or(np.abs(long_follow_step) > 0, np.abs(lat_follow_step) > 0)
    continue_mask = np.logical_not(follow_mask)
    
    new_edges[follow_mask, 1, 0] = new_edges[follow_mask, 0, 0] + long_follow_step[follow_mask]
    new_edges[follow_mask, 1, 1] = new_edges[follow_mask, 0, 1] + lat_follow_step[follow_mask]
    
    new_edges[continue_mask, 1, 0] = new_edges[continue_mask, 0, 0] + long_gaussian_step[continue_mask]
    new_edges[continue_mask, 1, 1] = new_edges[continue_mask, 0, 1] + lat_gaussian_step[continue_mask]
    
    return np.append(turtle_trajectories, new_edges, axis=0)
    


In [9]:
plt.rcParams['animation.ffmpeg_path']=r'F:\College\Senior\Fall\EPS 109\hw9\ffmpeg_2021\bin\ffmpeg.exe' 
metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
from matplotlib.animation import FFMpegWriter
writer = FFMpegWriter(fps=15, metadata=metadata)

In [10]:
simturtle_trajectories = generate_simturtle_initial_positions(n_turtles)
original_trajectories = get_original_turtle_paths(lines_raw_data_df)
turtle_trajectories = simturtle_trajectories
for i in range(0, timesteps):
    turtle_trajectories = step_simturtles(turtle_trajectories, n_turtles, original_trajectories)

fig = plt.figure(figsize=(15, 10))
fig.clear()
plt.gca().axis([-40, -10, -15, 0])
atlantic_ocean_bg_img = plt.imread('atlantic_ocean_bg.png')
plt.imshow(atlantic_ocean_bg_img, extent=[-40, -10, -15, 0])
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.title("Real and Simulated Turtle Movement from Brazil to Ascension Island, p_follow 1")
with writer.saving(fig, "animation1.mp4", dpi=200):
    for i in range(0, timesteps):
        lc_real = LineCollection(original_trajectories[:i*20], colors='r')
        plt.gca().add_collection(lc_real)
        lc = LineCollection(turtle_trajectories[:i*n_turtles], colors='y')
        plt.gca().add_collection(lc)
        plt.legend(['real turtles', 'sim turtles'], loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.01)
        writer.grab_frame()

In [11]:
probability_follow = 0.5


In [12]:
simturtle_trajectories = generate_simturtle_initial_positions(n_turtles)
original_trajectories = get_original_turtle_paths(lines_raw_data_df)
turtle_trajectories = simturtle_trajectories
for i in range(0, timesteps):
    turtle_trajectories = step_simturtles(turtle_trajectories, n_turtles, original_trajectories)

fig = plt.figure(figsize=(15, 10))
fig.clear()
plt.gca().axis([-40, -10, -15, 0])
atlantic_ocean_bg_img = plt.imread('atlantic_ocean_bg.png')
plt.imshow(atlantic_ocean_bg_img, extent=[-40, -10, -15, 0])
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.title("Real and Simulated Turtle Movement from Brazil to Ascension Island, p_follow 0.5")
with writer.saving(fig, "animation2.mp4", dpi=200):
    for i in range(0, timesteps):
        lc_real = LineCollection(original_trajectories[:i*20], colors='r')
        plt.gca().add_collection(lc_real)
        lc = LineCollection(turtle_trajectories[:i*n_turtles], colors='y')
        plt.gca().add_collection(lc)
        plt.legend(['real turtles', 'sim turtles'], loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.01)
        writer.grab_frame()

In [13]:
probability_follow = 0

In [14]:
simturtle_trajectories = generate_simturtle_initial_positions(n_turtles)
original_trajectories = get_original_turtle_paths(lines_raw_data_df)
turtle_trajectories = simturtle_trajectories
for i in range(0, timesteps):
    turtle_trajectories = step_simturtles(turtle_trajectories, n_turtles, original_trajectories)

fig = plt.figure(figsize=(15, 10))
fig.clear()
plt.gca().axis([-40, -10, -15, 0])
atlantic_ocean_bg_img = plt.imread('atlantic_ocean_bg.png')
plt.imshow(atlantic_ocean_bg_img, extent=[-40, -10, -15, 0])
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.title("Real and Simulated Turtle Movement from Brazil to Ascension Island, p_follow 0")
with writer.saving(fig, "animation3.mp4", dpi=200):
    for i in range(0, timesteps):
        lc_real = LineCollection(original_trajectories[:i*20], colors='r')
        plt.gca().add_collection(lc_real)
        lc = LineCollection(turtle_trajectories[:i*n_turtles], colors='y')
        plt.gca().add_collection(lc)
        plt.legend(['real turtles', 'sim turtles'], loc='upper left')
        plt.draw()
        plt.show()
        plt.pause(0.01)
        writer.grab_frame()